In [ ]:
!pip install transformers datasets trl bitsandbytes peft
!pip install datasets
!pip install -U accelerate

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.7/472.7 kB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.6/316.6 kB 16.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 122.4/122.4 MB 6.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.7/320.7 kB 13.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 109.8/109.8 kB 10.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 330.9/330.9 kB 11.4 MB/s eta 0:00:00
  Attempting uninstall: accelerate
    Found existing installation: accelerate 0.34.2
    Uninstalling accelerate-0.34.2:
      Successfully uninstalled accelerate-0.34.2


In [ ]:
import os
import torch
import torchvision
torchvision.disable_beta_transforms_warning()
from datasets import load_dataset, concatenate_datasets
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, BitsAndBytesConfig
from trl import SFTTrainer
from peft import LoraConfig, get_peft_model

# W&B 비활성화

In [ ]:
import os
os.environ["WANDB_MODE"] = "disabled"

In [ ]:
torch.cuda.empty_cache()
torch.cuda.memory_summary(device=None, abbreviated=False)


'|===========================================================================|\n|                  PyTorch CUDA memory summary, device ID 0                 |\n|---------------------------------------------------------------------------|\n|            CUDA OOMs: 0            |        cudaMalloc retries: 0         |\n|===========================================================================|\n|        Metric         | Cur Usage  | Peak Usage | Tot Alloc  | Tot Freed  |\n|---------------------------------------------------------------------------|\n| Allocated memory      |      0 B   |      0 B   |      0 B   |      0 B   |\n|       from large pool |      0 B   |      0 B   |      0 B   |      0 B   |\n|       from small pool |      0 B   |      0 B   |      0 B   |      0 B   |\n|---------------------------------------------------------------------------|\n| Active memory         |      0 B   |      0 B   |      0 B   |      0 B   |\n|       from large pool |      0 B   |      0 B   |

# 환경 변수 로드 및 Google Colab 환경 설정

In [ ]:
if os.path.exists('C:/Users/yd170/OneDrive/바탕 화면/Coding/KRX.env'):
    load_dotenv('C:/Users/yd170/OneDrive/바탕 화면/Coding/KRX.env')
    hf_token = os.getenv("HF_TOKEN")
else:
    hf_token = "YOUR_HF_TOKEN"

model_name = "Qwen/Qwen2-1.5B"
max_seq_length = 2048

# 양자화 설정 (4비트 양자화 사용)

In [ ]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,  # 4비트 양자화 적용
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.float16
)

# 모델 및 토크나이저 로드 (GPU 사용하도록 설정)

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(model_name, token=hf_token)
model = AutoModelForCausalLM.from_pretrained(model_name, quantization_config=bnb_config, device_map="auto")

# LoRA 설정 추가

In [ ]:
lora_config = LoraConfig(
    r=16,
    lora_alpha=32,
    target_modules=["q_proj", "v_proj"],
    lora_dropout=0.05,
    bias="none"
)
model = get_peft_model(model, lora_config)

# 두 개의 데이터셋 로드 및 병합

In [ ]:
first_dataset = load_dataset("amphora/krx-sample-instructions", split="train")
second_dataset = load_dataset("Cartinoe5930/web_text_synthetic_dataset_50k", split="train")

# 데이터셋 병합
dataset = concatenate_datasets([first_dataset, second_dataset])

# 프롬프트 포맷 설정
prompt_format = """Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.

### Instruction:
{}

### Response:
{}"""

EOS_TOKEN = tokenizer.eos_token

def formatting_prompts_func(examples):
    instructions = []
    outputs = []

    # 데이터셋 내 필드 확인 후 각 필드에 따라 처리
    if "prompt" in examples and "response" in examples:
        instructions = examples["prompt"]
        outputs = examples["response"]
    elif "question" in examples and "response" in examples:
        instructions = examples["question"]
        outputs = examples["response"]
    else:
        raise KeyError("The dataset fields do not match the expected format.")

    texts = [prompt_format.format(instr, output) + EOS_TOKEN for instr, output in zip(instructions, outputs)]
    return {"formatted_text": texts}

# 데이터셋 가공
dataset = dataset.map(formatting_prompts_func, batched=True)

# 모델 학습 설정

In [ ]:
training_args = TrainingArguments(
    output_dir="./output",
    per_device_train_batch_size=1,  d
    gradient_accumulation_steps=8,
    max_steps=100,
    logging_steps=10,
    learning_rate=2e-5,
    seed=42,
    save_steps=100,
    fp16=True, # 혼합 정밀도 사용으로 메모리 최적화
    report_to="none",
)

# GPU 메모리 관리 최적화 환경 변수 설정

In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"

# SFTTrainer 초기화

In [ ]:
trainer = SFTTrainer(
    model=model,
    tokenizer=tokenizer,
    train_dataset=dataset,  # 병합된 데이터셋 사용
    dataset_text_field="formatted_text",
    max_seq_length=1024,
    args=training_args,
)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': dataset_text_field, max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:283: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:321: UserWarning: You passed a `dataset_text_field` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(
max_steps is given, it will override any value given in num_train_epochs


# 학습

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
print("모델 학습 시작...")
trainer.train()
print("모델 학습 완료.")

# 학습된 모델 저장
print("모델 저장 중...")
model.save_pretrained("/content/drive/My Drive/KRX_Qwen2_1_5B")
print("모델 저장 완료.")

print("토크나이저 저장 중...")
tokenizer.save_pretrained("/content/drive/My Drive/KRX_Qwen2_1_5B")
print("토크나이저 저장 완료.")


모델 학습 시작...


모델 학습 완료.
모델 저장 중...
모델 저장 완료.
토크나이저 저장 중...
토크나이저 저장 완료.


# 학습된 모델 로드

In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM
from google.colab import drive

# Google Drive 마운트
drive.mount('/content/drive')

# 학습된 모델 로드 (Google Drive에서 저장된 경로 지정)
model_name = "/content/drive/My Drive/KRX_Qwen2_1_5B"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name)

print("모델과 토크나이저가 성공적으로 로드되었습니다.")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


모델과 토크나이저가 성공적으로 로드되었습니다.


# 추론을 위한 프롬프트 설정

In [ ]:
prompt_format = """The following is a detailed financial question or instruction, and the corresponding answer is expected to be precise and informative. Use relevant financial terms and provide a comprehensive explanation.

### Instruction:
{}

### Response:"""

# 예제 프롬프트

In [ ]:
instruction = "선물옵션에 대해 설명해줘."
prompt = prompt_format.format(instruction)
inputs = tokenizer(prompt, return_tensors="pt")

# 텍스트 생성

In [ ]:
outputs = model.generate(
    **inputs,
    max_new_tokens=256,
    temperature=0.7,         # 다양성 조절
    top_k=50,                # 최상위 K개의 단어만 고려
    repetition_penalty=1.2,  # 반복을 줄이기 위한 패널티
    use_cache=True
)

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:567: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.7` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
Setting `pad_token_id` to `eos_token_id`:151643 for open-end generation.


# 결과 출력

In [ ]:
response = tokenizer.decode(outputs[0], skip_special_tokens=True)

# 입력된 프롬프트 이후의 응답 부분만 출력
print(response[len(prompt):].strip())

Orange price at the port of origin?

Yes, that's correct! The term "orange" in this context refers to the orange fruit itself rather than its value as an investment asset.
